## CYP450 Bioactivation Simulation

In [3]:
# CYP450 Bioactivation Simulation: Styrene Docking (with Blind Docking)

# --- 1. SETUP AND IMPORTS ---
import os
import requests
import py3Dmol
import MDAnalysis as mda
from pdbfixer import PDBFixer
from openmm.app import PDBFile
from rdkit import Chem
from rdkit.Chem import AllChem, rdChemReactions
import subprocess

# --- 2. INITIAL CONFIGURATION AND FILE DOWNLOAD ---
pdb_id = "3e4e"
protein_directory = "docking_files"
protein_filename = f"{pdb_id}.pdb"
protein_filepath = os.path.join(protein_directory, protein_filename)

# Create directories for our files
os.makedirs(protein_directory, exist_ok=True)
os.makedirs(os.path.join(protein_directory, "ligand_structures"), exist_ok=True)
os.makedirs(os.path.join(protein_directory, "docking_results"), exist_ok=True)

# Download the PDB file if it doesn't exist
if not os.path.exists(protein_filepath):
    print(f"Downloading protein {pdb_id}...")
    protein_url = f"https://files.rcsb.org/download/{pdb_id}.pdb"
    protein_request = requests.get(protein_url)
    protein_request.raise_for_status()  # Check for download errors
    with open(protein_filepath, "w") as f:
        f.write(protein_request.text)
    print(f"Saved protein to {protein_filepath}")
else:
    print(f"Protein file {protein_filepath} already exists.")

# --- 3. PROTEIN AND LIGAND PREPARATION ---

# Load the universe with MDAnalysis
u = mda.Universe(protein_filepath)

# Extract the native ligand (4PZ) to use for comparison
native_ligand_path = os.path.join(protein_directory, "ligand_structures", "native_ligand.pdb")
native_ligand_select = "chainID A and resname 4PZ"
native_ligand = u.select_atoms(native_ligand_select)
if native_ligand.n_atoms > 0:
    native_ligand.write(native_ligand_path)
    print(f"Extracted native ligand to {native_ligand_path}")
else:
    raise ValueError("Native ligand '4PZ' not found in PDB. Cannot define active site for comparison.")

# Clean PDB to keep only protein and the essential HEM cofactor
clean_path = os.path.join(protein_directory, f"{pdb_id}_clean.pdb")
select_protein_heme = "protein or resname HEM"
clean_atoms = u.select_atoms(select_protein_heme)
clean_atoms.write(clean_path)
print(f"Cleaned PDB saved to {clean_path}")

# Use PDBFixer to add missing atoms and hydrogens
receptor_path = f"{protein_directory}/{pdb_id}_all_atom.pdb"
fixer = PDBFixer(filename=clean_path)
fixer.findMissingResidues()
fixer.findNonstandardResidues()
fixer.findMissingAtoms()
fixer.addMissingAtoms()
fixer.addMissingHydrogens(7.0)  # Add hydrogens at neutral pH
with open(receptor_path, 'w') as f:
    PDBFile.writeFile(fixer.topology, fixer.positions, f, True)
print(f"Prepared all-atom receptor saved to {receptor_path}")

# Prepare the styrene ligand from a SMILES string
styrene_smiles = "C=Cc1ccccc1"
styrene_mol = Chem.MolFromSmiles(styrene_smiles)
styrene_mol = Chem.AddHs(styrene_mol)
AllChem.EmbedMolecule(styrene_mol)
AllChem.MMFFOptimizeMolecule(styrene_mol)
styrene_path = os.path.join(protein_directory, "ligand_structures", "styrene.sdf")
with Chem.SDWriter(styrene_path) as writer:
    writer.write(styrene_mol)
print(f"Styrene ligand prepared and saved to {styrene_path}")

# --- 4. BLIND DOCKING EXECUTION ---

# Calculate the center and dimensions for the blind docking box
print("\nCalculating dimensions for blind docking...")
receptor_u = mda.Universe(receptor_path)
protein_atoms = receptor_u.select_atoms("protein")

# Calculate the center of mass of the protein
center = protein_atoms.center_of_mass()

# Calculate the full size of the protein and add a buffer
min_coords = protein_atoms.positions.min(axis=0)
max_coords = protein_atoms.positions.max(axis=0)
dimensions = max_coords - min_coords
size = dimensions + 5.0  # Add a 5 Angstrom buffer

print(f"Box Center (x,y,z): {center[0]:.2f}, {center[1]:.2f}, {center[2]:.2f}")
print(f"Box Size   (x,y,z): {size[0]:.2f}, {size[1]:.2f}, {size[2]:.2f}")

# Define the output file for the blind dock results
blind_docked_sdf = f"{protein_directory}/docking_results/styrene_docked_3e4e_blind.sdf"

# Construct the GNINA command for blind docking
gnina_cmd_blind = [
    "docker", "run", "--platform", "linux/amd64", "-v", f"{os.getcwd()}:/work", "-w", "/work",
    "gnina/gnina", "gnina",
    "-r", receptor_path,
    "-l", styrene_path,
    # Manually define the search box for blind docking
    "--center_x", f"{center[0]:.3f}",
    "--center_y", f"{center[1]:.3f}",
    "--center_z", f"{center[2]:.3f}",
    "--size_x", f"{size[0]:.3f}",
    "--size_y", f"{size[1]:.3f}",
    "--size_z", f"{size[2]:.3f}",
    "-o", blind_docked_sdf,
    "--seed", "42",
    # A higher exhaustiveness is recommended for the much larger search space
    "--exhaustiveness", "100" 
]

print("\nRunning Blind Docking with GNINA... (This may take a while)")
subprocess.run(gnina_cmd_blind, check=True)
print(f"Blind docking complete. Results saved to {blind_docked_sdf}")


# --- 5. VISUALIZATION OF RESULTS ---

def visualize_poses(receptor_pdb, docked_sdf, cognate_file=None, animate=False):
    """Function to visualize the protein, docked poses, and native ligand."""
    v = py3Dmol.view(width=600, height=500)
    v.addModel(open(receptor_pdb).read(), 'pdb')
    v.setStyle({'cartoon': {'color': 'spectrum'}})
    
    # Highlight the heme group, the catalytic center
    v.setStyle({'resn': 'HEM'}, {'stick': {'colorscheme': 'redCarbon', 'radius': 0.2}})
    
    # Add the native ligand for reference (where it *should* bind)
    if cognate_file and os.path.exists(cognate_file):
        v.addModel(open(cognate_file).read(), 'pdb')
        v.setStyle({'model': 1}, {'stick': {'color': 'green', 'radius': 0.2}})
    
    # Add the docked poses from the blind dock
    with open(docked_sdf) as f:
        sdf_content = f.read()
    v.addModelsAsFrames(sdf_content, 'sdf')
    v.setStyle({'model': -1}, {'stick': {'colorscheme': 'blueCarbon', 'radius': 0.2}})
    
    v.zoomTo({'resn': 'HEM'})
    
    if animate:
        v.animate({'loop': 'forward'})
        
    return v

# Visualize the results of the blind docking
print("\nCreating visualization of blind docking results...")
print("Heme (catalytic site) is red, native ligand (reference) is green, docked styrene is blue.")
v_blind = visualize_poses(receptor_path,
                          blind_docked_sdf,
                          cognate_file=native_ligand_path,
                          animate=True)
v_blind.show()


Protein file docking_files/3e4e.pdb already exists.
Extracted native ligand to docking_files/ligand_structures/native_ligand.pdb
Cleaned PDB saved to docking_files/3e4e_clean.pdb


/opt/anaconda3/envs/moldock/lib/python3.11/site-packages/MDAnalysis/coordinates/PDB.py:1154: UserWarning: Found no information for attr: 'formalcharges' Using default value of '0'
  warnings.warn("Found no information for attr: '{}'"


Prepared all-atom receptor saved to docking_files/3e4e_all_atom.pdb
Styrene ligand prepared and saved to docking_files/ligand_structures/styrene.sdf

Calculating dimensions for blind docking...
Box Center (x,y,z): 20.03, 15.56, 22.56
Box Size   (x,y,z): 104.17, 104.97, 77.06

Running Blind Docking with GNINA... (This may take a while)

== CUDA ==

CUDA Version 12.3.2

Container image Copyright (c) 2016-2023, NVIDIA CORPORATION & AFFILIATES. All rights reserved.

This container image and its contents are governed by the NVIDIA Deep Learning Container License.
By pulling and using the container, you accept the terms and conditions of this license:
https://developer.nvidia.com/ngc/nvidia-deep-learning-container-license

A copy of this license is made available in this container at /NGC-DL-CONTAINER-LICENSE for your convenience.

   Use the NVIDIA Container Toolkit to start this container with GPU support; see
   https://docs.nvidia.com/datacenter/cloud-native/ .

              _          

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [4]:
# CYP450 Bioactivation Simulation: Styrene Docking (with Blind Docking)

# --- 1. SETUP AND IMPORTS ---
import os
import requests
import py3Dmol
import MDAnalysis as mda
from pdbfixer import PDBFixer
from openmm.app import PDBFile
from rdkit import Chem
from rdkit.Chem import AllChem, rdChemReactions
import subprocess

# --- 2. INITIAL CONFIGURATION AND FILE DOWNLOAD ---
pdb_id = "3e4e"
protein_directory = "docking_files"
protein_filename = f"{pdb_id}.pdb"
protein_filepath = os.path.join(protein_directory, protein_filename)

# Create directories for our files
os.makedirs(protein_directory, exist_ok=True)
os.makedirs(os.path.join(protein_directory, "ligand_structures"), exist_ok=True)
os.makedirs(os.path.join(protein_directory, "docking_results"), exist_ok=True)

# Download the PDB file if it doesn't exist
if not os.path.exists(protein_filepath):
    print(f"Downloading protein {pdb_id}...")
    protein_url = f"https://files.rcsb.org/download/{pdb_id}.pdb"
    protein_request = requests.get(protein_url)
    protein_request.raise_for_status()  # Check for download errors
    with open(protein_filepath, "w") as f:
        f.write(protein_request.text)
    print(f"Saved protein to {protein_filepath}")
else:
    print(f"Protein file {protein_filepath} already exists.")

# --- 3. PROTEIN AND LIGAND PREPARATION ---

# Load the universe with MDAnalysis
u = mda.Universe(protein_filepath)

# Extract the native ligand (4PZ) to use for comparison
native_ligand_path = os.path.join(protein_directory, "ligand_structures", "native_ligand.pdb")
native_ligand_select = "chainID A and resname 4PZ"
native_ligand = u.select_atoms(native_ligand_select)
if native_ligand.n_atoms > 0:
    native_ligand.write(native_ligand_path)
    print(f"Extracted native ligand to {native_ligand_path}")
else:
    raise ValueError("Native ligand '4PZ' not found in PDB. Cannot define active site for comparison.")

# Clean PDB to keep only protein and the essential HEM cofactor
clean_path = os.path.join(protein_directory, f"{pdb_id}_clean.pdb")
select_protein_heme = "protein or resname HEM"
clean_atoms = u.select_atoms(select_protein_heme)
clean_atoms.write(clean_path)
print(f"Cleaned PDB saved to {clean_path}")

# Use PDBFixer to add missing atoms and hydrogens
receptor_path = f"{protein_directory}/{pdb_id}_all_atom.pdb"
fixer = PDBFixer(filename=clean_path)
fixer.findMissingResidues()
fixer.findNonstandardResidues()
fixer.findMissingAtoms()
fixer.addMissingAtoms()
fixer.addMissingHydrogens(7.0)  # Add hydrogens at neutral pH
with open(receptor_path, 'w') as f:
    PDBFile.writeFile(fixer.topology, fixer.positions, f, True)
print(f"Prepared all-atom receptor saved to {receptor_path}")

# Prepare the styrene ligand from a SMILES string and save as .xyz
styrene_smiles = "C=Cc1ccccc1"
styrene_mol = Chem.MolFromSmiles(styrene_smiles)
styrene_mol = Chem.AddHs(styrene_mol)
AllChem.EmbedMolecule(styrene_mol)
AllChem.MMFFOptimizeMolecule(styrene_mol)
styrene_path = os.path.join(protein_directory, "ligand_structures", "cpd.xyz")
with open(styrene_path, 'w') as f:
    conf = styrene_mol.GetConformer()
    f.write(str(styrene_mol.GetNumAtoms()) + '\n')
    f.write('Styrene\n')
    for atom in styrene_mol.GetAtoms():
        pos = conf.GetAtomPosition(atom.GetIdx())
        f.write(f"{atom.GetSymbol()} {pos.x:.3f} {pos.y:.3f} {pos.z:.3f}\n")
print(f"Styrene ligand prepared and saved to {styrene_path}\"")

# --- 4. BLIND DOCKING EXECUTION ---

# Calculate the center and dimensions for the blind docking box
print("\nCalculating dimensions for blind docking...")
receptor_u = mda.Universe(receptor_path)
protein_atoms = receptor_u.select_atoms("protein")

# Calculate the center of mass of the protein
center = protein_atoms.center_of_mass()

# Calculate the full size of the protein and add a buffer
min_coords = protein_atoms.positions.min(axis=0)
max_coords = protein_atoms.positions.max(axis=0)
dimensions = max_coords - min_coords
size = dimensions + 5.0  # Add a 5 Angstrom buffer

print(f"Box Center (x,y,z): {center[0]:.2f}, {center[1]:.2f}, {center[2]:.2f}")
print(f"Box Size   (x,y,z): {size[0]:.2f}, {size[1]:.2f}, {size[2]:.2f}")

# Define the output file for the blind dock results
blind_docked_sdf = f"{protein_directory}/docking_results/styrene_docked_3e4e_blind.sdf"

# Construct the GNINA command for blind docking
gnina_cmd_blind = [
    "docker", "run", "--platform", "linux/amd64", "-v", f"{os.getcwd()}:/work", "-w", "/work",
    "gnina/gnina", "gnina",
    "-r", receptor_path,
    "-l", styrene_path,
    # Manually define the search box for blind docking
    "--center_x", f"{center[0]:.3f}",
    "--center_y", f"{center[1]:.3f}",
    "--center_z", f"{center[2]:.3f}",
    "--size_x", f"{size[0]:.3f}",
    "--size_y", f"{size[1]:.3f}",
    "--size_z", f"{size[2]:.3f}",
    "-o", blind_docked_sdf,
    "--seed", "42",
    # A higher exhaustiveness is recommended for the much larger search space
    "--exhaustiveness", "100" 
]

print("\nRunning Blind Docking with GNINA... (This may take a while)")
subprocess.run(gnina_cmd_blind, check=True)
print(f"Blind docking complete. Results saved to {blind_docked_sdf}")


# --- 5. VISUALIZATION OF RESULTS ---

def visualize_poses(receptor_pdb, docked_sdf, cognate_file=None, animate=False):
    """Function to visualize the protein, docked poses, and native ligand."""
    v = py3Dmol.view(width=600, height=500)
    v.addModel(open(receptor_pdb).read(), 'pdb')
    v.setStyle({'cartoon': {'color': 'spectrum'}})
    
    # Highlight the heme group, the catalytic center
    v.setStyle({'resn': 'HEM'}, {'stick': {'colorscheme': 'redCarbon', 'radius': 0.2}})
    
    # Add the native ligand for reference (where it *should* bind
    if cognate_file and os.path.exists(cognate_file):
        v.addModel(open(cognate_file).read(), 'pdb')
        v.setStyle({'model': 1}, {'stick': {'color': 'green', 'radius': 0.2}})
    
    # Add the docked poses from the blind dock
    with open(docked_sdf) as f:
        sdf_content = f.read()
    v.addModelsAsFrames(sdf_content, 'sdf')
    v.setStyle({'model': -1}, {'stick': {'colorscheme': 'blueCarbon', 'radius': 0.2}})
    
    v.zoomTo({'resn': 'HEM'})
    
    if animate:
        v.animate({'loop': 'forward'})
        
    return v

# Visualize the results of the blind docking
print("\nCreating visualization of blind docking results...")
print("Heme (catalytic site) is red, native ligand (reference) is green, docked styrene is blue.")
v_blind = visualize_poses(receptor_path,
                          blind_docked_sdf,
                          cognate_file=native_ligand_path,
                          animate=True)
v_blind.show()

Protein file docking_files/3e4e.pdb already exists.
Extracted native ligand to docking_files/ligand_structures/native_ligand.pdb
Cleaned PDB saved to docking_files/3e4e_clean.pdb


/opt/anaconda3/envs/moldock/lib/python3.11/site-packages/MDAnalysis/coordinates/PDB.py:1154: UserWarning: Found no information for attr: 'formalcharges' Using default value of '0'
  warnings.warn("Found no information for attr: '{}'"


Prepared all-atom receptor saved to docking_files/3e4e_all_atom.pdb
Styrene ligand prepared and saved to docking_files/ligand_structures/cpd.xyz"

Calculating dimensions for blind docking...
Box Center (x,y,z): 20.03, 15.56, 22.56
Box Size   (x,y,z): 104.05, 104.91, 76.83

Running Blind Docking with GNINA... (This may take a while)

== CUDA ==

CUDA Version 12.3.2

Container image Copyright (c) 2016-2023, NVIDIA CORPORATION & AFFILIATES. All rights reserved.

This container image and its contents are governed by the NVIDIA Deep Learning Container License.
By pulling and using the container, you accept the terms and conditions of this license:
https://developer.nvidia.com/ngc/nvidia-deep-learning-container-license

A copy of this license is made available in this container at /NGC-DL-CONTAINER-LICENSE for your convenience.

   Use the NVIDIA Container Toolkit to start this container with GPU support; see
   https://docs.nvidia.com/datacenter/cloud-native/ .

              _             

3Dmol.js failed to load for some reason. Please check your browser console for error messages.